In [1]:
path = '/home/vscode/workspace/traces/session_main_2/ust/uid/12810/64-bit/'

In [2]:
import sys
# Add paths to tracetools_analysis and tracetools_read.
# There are two options:
#   1. from source, assuming a workspace with:
#       src/tracetools_analysis/
#       src/ros2/ros2_tracing/tracetools_read/
sys.path.insert(0, '../')
sys.path.insert(0, '../../../ros2/ros2_tracing/tracetools_read/')
#   2. from Debian packages, setting the right ROS 2 distro:
#ROS_DISTRO = 'rolling'
#sys.path.insert(0, f'/opt/ros/{ROS_DISTRO}/lib/python3.8/site-packages')
import datetime as dt

from bokeh.plotting import figure
from bokeh.plotting import output_notebook
from bokeh.io import show
from bokeh.layouts import row
from bokeh.models import ColumnDataSource
from bokeh.models import DatetimeTickFormatter
from bokeh.models import PrintfTickFormatter
import numpy as np
import pandas as pd

from tracetools_analysis.loading import load_file
from tracetools_analysis.processor.ros2 import Ros2Handler
from tracetools_analysis.utils.ros2 import Ros2DataModelUtil

In [3]:
events = load_file(path)

converting trace directory: /home/vscode/workspace/traces/session_main_1/ust/uid/12810/64-bit
converted 0 events in 1 ms
output written to: /home/vscode/workspace/traces/session_main_1/ust/uid/12810/64-bit/converted


In [20]:
handler = Ros2Handler().process(events)

 [100%] [Ros2Handler]


In [21]:
data_util = Ros2DataModelUtil(handler.data)

In [19]:
output_notebook()
psize = 450
colours = ['#29788E', '#DD4968', '#410967']

Loading BokehJS ...

In [22]:
callback_symbols = data_util.get_callback_symbols()

In [34]:
from numpy import timedelta64


# plot difference between starts of callbacks

earliest_date = None
for obj, symbol in callback_symbols.items():
    duration_df = data_util.get_callback_durations(obj)
    thedate = duration_df.loc[:, 'timestamp'].iloc[0]
    if earliest_date is None or thedate <= earliest_date:
        earliest_date = thedate

starttime = earliest_date.strftime('%Y-%m-%d %H:%M')

duration = figure(
    title='Callback start delta',
    x_axis_label=f'start ({starttime})',
    y_axis_label='time since start (ms)',
    width=psize, height=psize,
)

colour_i = 0
for obj, symbol in [*callback_symbols.items()][:1]:
    # Filter out internal subscriptions
    owner_info = data_util.get_callback_owner_info(obj)
    if not owner_info or '/parameter_events' in owner_info:
        continue

    duration_df = data_util.get_callback_durations(obj)

    # sort by timestamp
    duration_df = duration_df.sort_values(by='timestamp')

    # calculate time since previous start
    duration_df['delta'] = duration_df['timestamp'].diff()
    duration_df['delta'] = duration_df['delta'].fillna(timedelta64(0))
    duration_df['delta'] = duration_df['delta'].dt.total_seconds() * 1000 # convert to ms

    #print the average and max
    print(f'{symbol}:')
    print(f'  avg: {duration_df["delta"].mean()}')
    print(f'  max: {duration_df["delta"].max()}')

    source = ColumnDataSource(duration_df)
    duration.title.align = 'center'
    duration.line(
        x='timestamp',
        y='delta',
        legend_label=str(symbol),
        line_width=2,
        source=source,
        line_color=colours[colour_i],
    )
    colour_i += 1
    duration.legend.label_text_font_size = '11px'
    duration.xaxis[0].formatter = DatetimeTickFormatter(seconds='%Ss')
    
    duration.line(
        x=[duration_df['timestamp'].iloc[0], duration_df['timestamp'].iloc[-1]],
        y=[duration_df['delta'].mean(), duration_df['delta'].mean()],
        line_width=2,
        line_color=colours[colour_i],
    )
    duration.line(
        x=[duration_df['timestamp'].iloc[0], duration_df['timestamp'].iloc[-1]],
        y=[duration_df['delta'].max(), duration_df['delta'].max()],
        line_width=2,
        line_color=colours[colour_i],
    )

show(duration)
    

TestNode::TestNode()::{lambda()#1}:
  avg: 0.16915256160007172
  max: 0.574819
